In [1]:
!apt-get install -y python-numpy python-dev cmake zlib1g-dev libjpeg- dev xvfb libav-tools xorg-dev python-opengl libboost-all-dev libsdl2-dev swig

'apt-get' is not recognized as an internal or external command,
operable program or batch file.


In [4]:
!apt install xvfb -y

Reading package lists... Done
Building dependency tree       
Reading state information... Done
xvfb is already the newest version (2:1.19.6-1ubuntu4.3).
The following package was automatically installed and is no longer required:
  libnvidia-common-430
Use 'apt autoremove' to remove it.
0 upgraded, 0 newly installed, 0 to remove and 7 not upgraded.


In [5]:
!apt-get install python-opengl -y

Reading package lists... Done
Building dependency tree       
Reading state information... Done
python-opengl is already the newest version (3.1.0+dfsg-1).
The following package was automatically installed and is no longer required:
  libnvidia-common-430
Use 'apt autoremove' to remove it.
0 upgraded, 0 newly installed, 0 to remove and 7 not upgraded.


In [6]:
!pip install pyvirtualdisplay 
!pip install piglet

In [3]:
import os
import numpy as np
from keras.optimizers import Adam, RMSprop
from keras.models import Sequential, Model
from keras.layers import Dense, Conv2D, Flatten
from keras.initializers import VarianceScaling
from random import random, randrange, randint

import gym, random, os.path, math, glob, csv, base64
from pathlib import Path
from gym import wrappers
import matplotlib.pyplot as plt
from keras.utils import plot_model

from stable_baselines.common.policies import MlpPolicy
from stable_baselines.common.vec_env import VecVideoRecorder, SubprocVecEnv, DummyVecEnv
from stable_baselines import PPO2

ModuleNotFoundError: No module named 'keras'

In [0]:
import os
import time

class Logger:
    def __init__(self, debug=False, append=None, custom_run_name=None):
        self.debug = debug
        if self.debug:
            return

        output_folder = './output/'
        run_folder = 'run%Y%m%d-%H%M%S' if custom_run_name is None else custom_run_name
        if not os.path.exists(output_folder):
            os.makedirs(output_folder)
        self.path = ''.join([output_folder, time.strftime(run_folder)])
        if append is not None:
            self.path += '_' + str(append)
        self.path += '/'
        if not os.path.exists(self.path):
            os.makedirs(self.path)

        self.save_file = self.path + 'model.h5'

    def log(self, data):
        if not self.debug:
            try:
                logfile = open(self.path + 'log.txt', 'a')
            except IOError:
                print ('Logger:log IO error while opening log file', self.path, 'log.txt')
                return
            if type(data) is dict:
                for k in data:
                    logfile.write(k + ': ' + str(data[k]) + '\n')
                    print (k, ': ', data[k])
            elif type(data) is tuple:
                logfile.write(data[0] + ': ' + str(data[1]) + '\n')
            elif type(data) is str:
                logfile.write(data + '\n')
            elif type(data) is list:
                logfile.write(','.join(str(elem) for elem in data) + '\n')
        print(data)

    def to_csv(self, filename, row):
        if not self.debug:
            try:
                f = open(self.path + filename, 'a')
            except IOError:
                print ('Logger:to_csv IO error while opening file', self.path + filename)
                return
            if type(row) is list:
                string = ','.join([str(val) for val in row])
            elif type(row) is str:
                string = row
            else:
                string = str(row)  # Try to convert it anyway
            string = string + '\n' if not string.endswith('\n') else ''
            f.write(string)
            f.close()

In [0]:
class DeepQNetwork(object):
  def __init__(self, total_action, learning_rate=0.00025,
               input_dimension=(210, 160, 4), dropout_prob=0.1,
               batch_size=32, discount_factor=0.99,
               load_path=None, logger=None):
    # Parameters
    self.total_action = total_action
    self.learning_rate = learning_rate
    self.dropout_prob = dropout_prob
    self.batch_size=batch_size
    self.discount_factor=discount_factor
    self.training_file = 'training.csv'
    self.logger = logger
    self.input_dimension = input_dimension
    self.load_path = load_path

    # Init DQN
    self.model = self.build_network()
    self.target_model = self.build_network()

    if load_path is not None:
      self.model.load_weights(self.load_path)

    if self.logger is not None:
      self.logger.to_csv(self.training_file, 'Loss,Accuracy')

  # Clear
  def build_network(self):
    # CNN
    model = Sequential()
    model.add(Conv2D(32, 
                      kernel_size=8, 
                      strides=(4, 4),
                      activation='relu',
                      data_format = 'channels_first',
                      input_shape=self.input_dimension,
                      kernel_initializer=VarianceScaling(scale=2.0)))
    model.add(Conv2D(64, 
                      kernel_size=4, 
                      strides=(2, 2), 
                      activation='relu',
                      data_format = 'channels_first',
                      input_shape=self.input_dimension,
                      kernel_initializer=VarianceScaling(scale=2.0)))
    model.add(Conv2D(64, 
                      kernel_size=3, 
                      strides=(1, 1),
                      activation='relu',
                      data_format = 'channels_first',
                      input_shape=self.input_dimension,))
    
    model.add(Flatten())
    model.add(Dense(512, 
                    activation='relu',
                    kernel_initializer=VarianceScaling(scale=2.0)))
    model.add(Dense(units=self.total_action,
                    kernel_initializer=VarianceScaling(scale=2.0)))
    
    if self.load_path is not None:
      self.logger.log('Loading weights from file...')
      model.load_weights(self.load_path)

    model.compile(RMSprop(self.learning_rate),
                  loss='mean_squared_error', 
                  metrics=['accuracy'])
    return model

  def train(self, batch, target):
    s_train, q_train = [], []
    
    for experience in batch:
      s_train.append(experience['state'].astype(np.float64))

      next_state = experience['next'].astype(np.float64)
      next_state_predict = target.predict(next_state).ravel()
      next_q = np.max(next_state_predict)

      q_list = list(self.predict(experience['state'])[0])
      if not experience['terminate']:
        q_list[experience['action']] = experience['reward'] + self.discount_factor * next_q
      else:
        q_list[experience['action']] = experience['reward']
      q_train.append(q_list)
    
    s_train = np.asarray(s_train).squeeze()
    q_train = np.asarray(q_train).squeeze()

    r = self.model.fit(s_train, q_train, batch_size=self.batch_size, epochs=1, verbose=2)

    if self.logger is not None:
      self.logger.to_csv(self.training_file, [r.history['loss'][0], r.history['acc'][0]])

  def predict(self, state):
      state = state.astype(np.float64)
      return self.model.predict(state, batch_size=1)

  def save(self, filename=None, append=''):
      f = ('model%s.h5' % append) if filename is None else filename
      if self.logger is not None:
          self.logger.log('Saving model as %s' % f)
      self.model.save_weights(self.logger.path + f)

In [0]:
class Agent(object):
    def __init__(self, total_action, 
                 learning_rate=0.00025, input_dimension=(210, 160, 4),
                 batch_size=32, discount_factor=0.99,
                 memory_size=1024, dropout_prob=0.1,
                 epsilon=1, epsilon_decay=0.99,               
                 load_path=None, logger=None):
        # Hyper parameters
        self.total_action = total_action
        self.learning_rate = learning_rate
        self.input_dimension = input_dimension
        self.discount_factor = discount_factor
        self.dropout_prob = dropout_prob
        self.epsilon = epsilon
        self.epsilon_decay = epsilon_decay
        self.logger = logger
        self.load_path = load_path

        # Initialize memory
        self.batch_size = batch_size
        self.memory_size = memory_size
        self.memory = []
        self.memory_count = 0
        self.training_count = 0

        # Initialize network model
        self.networks = DeepQNetwork(self.total_action, 
                                  learning_rate=self.learning_rate,
                                  input_dimension=self.input_dimension, 
                                  dropout_prob=self.dropout_prob,
                                  batch_size=self.batch_size,
                                  discount_factor=self.discount_factor,
                                  load_path=self.load_path,
                                  logger=self.logger)
        self.networks.target_model.set_weights(self.networks.model.get_weights())
        
    # Storing transition into memory
    def store_transition(self, state, action, reward, next, terminate):
        exp = ({'state': state, 
                'action': action, 
                'reward': reward, 
                'next': next, 
                'terminate': terminate})
        
        if len(self.memory) >= self.memory_size:
            self.memory.popleft()
        self.memory.append(exp)

        # Periodically log how many samples we've gathered so far
        if (len(self.memory) % 100 == 0) and (len(self.memory) < self.memory_size) and (self.logger is not None):
            self.logger.log("Gathered %d samples of %d" %
                            (len(self.memory), self.memory_size))

    # Policy
    def choose_action(self, state, testing=False):
        epsilon = 0.05 if testing else self.epsilon
        if random.random() <= epsilon:
            action = np.random.choice(self.total_action)
        else:
            q_val = self.networks.predict(state)
            action = np.argmax(q_val)
        return action

    def update_epsilon(self):
      if self.epsilon - self.epsilon_decay > 0.1:
        self.epsilon -= self.epsilon_decay
      else:
        self.epsilon = 0.1

    def get_state(self):
      return self.memory[randrange(0, len(self.memory))]['state']

    # Sampling
    def sample_exp_batch(self):
        batch = []
        for i in range(self.batch_size):
          batch.append(self.memory[randrange(0, len(self.memory))])
        return np.asarray(batch)

    def max_q(self, state):
      q_values = self.networks.model.predict(state)
      idxs = np.argwhere(q_values == np.max(q_values)).ravel()
      return np.random.choice(idxs)

    # Learning with Experience Replay
    def learn(self):
      self.training_count += 1
      print('Training #', self.training_count)
      batch = self.sample_exp_batch()
      self.networks.train(batch, self.networks.target_model)

    def quit(self):
      if self.load_path is None:
        if self.logger is not None:
          self.logger.log('Quitting...')
        self.DQN.save(append='_DQN')
        self.DQN_target.save(append='_DQN_target')


In [11]:
from PIL import Image
from pyvirtualdisplay import Display
from IPython import display as ipythondisplay
from IPython.display import clear_output
from gym.wrappers import Monitor

display = Display(visible=0, size=(1400, 900))
display.start()

IMG_SIZE = None

def show_video():
    html = []
    for mp4 in Path("videos").glob("*.mp4"):
        video_b64 = base64.b64encode(mp4.read_bytes())
        html.append('''<video alt="{}" autoplay 
                      loop controls style="height: 400px;">
                      <source src="data:video/mp4;base64,{}" type="video/mp4" />
                 </video>'''.format(mp4, video_b64.decode('ascii')))
    ipythondisplay.display(ipythondisplay.HTML(data="<br>".join(html)))

def preprocess(observation):
  global IMG_SIZE
  image = Image.fromarray(observation, 'RGB').convert('L').resize(IMG_SIZE)
  file_name = 'preprocess size.png'
  image.save(file_name)
  image.show()
  print('image size[1]:', image.size[1])
  print('image size[0]:', image.size[0])
  return np.asarray(image.getdata(), dtype=np.uint8).reshape(image.size[1],
                                                              image.size[0])

def shift(current_stack, observation):
  return np.append(current_stack[1:], [observation], axis=0)

xdpyinfo was not found, X start can not be checked! Please install xdpyinfo!


In [0]:
from __future__ import print_function
max_mean_score = 0

def evaluate(DQA):
  global max_mean_score

  evaluation_csv = 'evaluation.csv'
  logger.to_csv(evaluation_csv, 'length,score')
  env = gym.make('Breakout-v0')
  env = Monitor(env, './videos', force=True, video_callable=lambda episode: True)
  scores = list()
  frame_counter = 0

  while frame_counter < 135000:
      obs = preprocess(env.reset())

      frame_counter += 1
      # Initialize the first state with the same 4 images
      current_state = np.array([obs, obs, obs, obs])
      t = 0
      episode = 0
      score = 0
      done = False

      # Start episode
      while not done:
          action = DQA.choose_action(np.asarray([current_state]),
                                  testing=True)
          obs, reward, done, info = env.step(action)
          obs = utils.preprocess_observation(obs)
          current_state = shift(current_state, obs)
          score += reward
          t += 1
          frame_counter += 1

          # End episode
          if done:
              episode += 1
              print('Episode %d end\n---------------\nFrame counter: %d\n' % 
                    (episode, frame_counter))
              print('Length: %d\n, Score: %f\n\n' % (t, score))
              # Save episode data in the evaluation csv
              logger.to_csv(evaluation_csv, [t, score])
              break
              
      scores.append([t, score])

  scores = np.asarray(scores)
  max_indices = np.argwhere(scores[:, 1] == np.max(scores[:, 1])).ravel()
  max_idx = np.random.choice(max_indices)

  # Save best model
  if max_mean_score < np.mean(scores):
      max_mean_score = np.mean(scores)
      agent.networks.save(append='_best')

  return scores[max_idx, :].ravel()

In [0]:
ALPHA = 0.00025
EPSILON = 1
EPSILON_DECAY = 9e-7
GAMMA = 0.99
INPUT_DIMS = (4, 110, 84)
BATCH_SIZE = 32
MEMORY_SIZE = 1024
MAX_EPISODE = 50000
DROPOUT_PROB = 0.
ENV_ID = 'MsPacmanDeterministic-v4'

IMG_SIZE = (84, 110)

if __name__ == '__main__':
  # Setup
  logger = Logger(debug=True, append=ENV_ID)

  # Environment
  env = gym.make(ENV_ID)
  env = Monitor(env, './videos', force=True, video_callable=lambda episode: True)
  agent = Agent(env.action_space.n, learning_rate=ALPHA, 
                input_dimension=INPUT_DIMS, dropout_prob=DROPOUT_PROB,
                batch_size=BATCH_SIZE, discount_factor=GAMMA, 
                memory_size=MEMORY_SIZE, epsilon=EPSILON,  
                epsilon_decay=EPSILON_DECAY, load_path=None, logger=logger)
  logger.log({
    'Action space': env.action_space.n,
    'Observation space': env.observation_space.shape
  })

  # Containers
  score_array = []
  mean_array = []
  state_array = []
  q_array = []

  # Counters
  episode_counter = 0
  frame_counter = 0

  #Main
  while episode_counter < MAX_EPISODE:
    score = 0
    observation = preprocess(env.reset())
    stacked_frames = np.array([observation, observation, observation, observation])
    #stacked_frames = np.reshape([stacked_frames], (1, 84, 84, 4))
    
    timestep = 0
    done = False
    frame_counter += 1
    print('Episode:', episode_counter)
    while not done:
      print('Timestep:', timestep)
      show_video()
      # Choose an action
      action = agent.choose_action(np.asarray([stacked_frames]))
      print('Action:', action)
      print('Stacked Frames[0]: ', stacked_frames[0])

      # Get next observation area and shift the stacked frames
      observation, reward, done, info = env.step(action)
      observation = preprocess(observation)
      print('Obs length:', len(observation))
      next_state = shift(stacked_frames, observation)

      frame_counter += 1

      # Store experience
      clip = np.clip(reward, -1, 1)
      agent.store_transition(np.asarray([stacked_frames]), action, 
                             clip, np.asarray([next_state]), done)
      
      # Train
      if len(agent.memory) >= 500:
        if timestep % 4 == 0:
          agent.learn()

        if agent.training_count % 500 == 0 and agent.training_count >= 500:
          agent.networks.target_model.set_weights(agent.networks.model.get_weights())

        if agent.training_count % 500 == 0 and agent.training_count >= 500:
            logger.to_csv(test_csv,
                          [np.mean(score_array), np.mean(mean_array)])
            del score_array[:]
            del mean_array[:]

        agent.update_epsilon()
      
      stacked_frames = next_state
      score += reward

      timestep+=1

      if frame_counter % 2000 == 0:
        t_evaluation, score_evaluation = evaluate(agent)

      if len(state_array) < 30:
        for x in range(random.randint(1, 5)):
          state_array.append(agent.memory[randrange(0, len(agent.memory))]['state'])
      else:
        score_array.append(score)
        q_array = [agent.max_q(state) for state in state_array]
        mean_array.append(np.mean(q_array))
    
    episode_counter += 1
  
  logger.log(evaluate(agent))












{'Action space': 9, 'Observation space': (210, 160, 3)}
image size[1]: 110
image size[0]: 84
Episode: 0
Timestep: 0


Action: 5
Stacked Frames[0]:  [[  0   0   0 ...   0   0   0]
 [145 145  31 ...  31 145 145]
 [145 145  31 ...  31 145 145]
 ...
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]]
image size[1]: 110
image size[0]: 84
Obs length: 110
Timestep: 1


Action: 2
Stacked Frames[0]:  [[  0   0   0 ...   0   0   0]
 [145 145  31 ...  31 145 145]
 [145 145  31 ...  31 145 145]
 ...
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]]
image size[1]: 110
image size[0]: 84
Obs length: 110
Timestep: 2


Action: 6
Stacked Frames[0]:  [[  0   0   0 ...   0   0   0]
 [145 145  31 ...  31 145 145]
 [145 145  31 ...  31 145 145]
 ...
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]]
image size[1]: 110
image size[0]: 84
Obs length: 110
Timestep: 3


Action: 5
Stacked Frames[0]:  [[  0   0   0 ...   0   0   0]
 [145 145  31 ...  31 145 145]
 [145 145  31 ...  31 145 145]
 ...
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]]
image size[1]: 110
image size[0]: 84
Obs length: 110
Timestep: 4


...

Action: 4
Stacked Frames[0]:  [[  0   0   0 ...   0   0   0]
 [145 145  31 ...  31 145 145]
 [145 145  31 ...  31 145 145]
 ...
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]]
image size[1]: 110
image size[0]: 84
Obs length: 110
Timestep: 30


Action: 2
Stacked Frames[0]:  [[  0   0   0 ...   0   0   0]
 [145 145  31 ...  31 145 145]
 [145 145  31 ...  31 145 145]
 ...
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]]
image size[1]: 110
image size[0]: 84
Obs length: 110
Timestep: 31


Action: 3
Stacked Frames[0]:  [[  0   0   0 ...   0   0   0]
 [145 145  31 ...  31 145 145]
 [145 145  31 ...  31 145 145]
 ...
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]]
image size[1]: 110
image size[0]: 84
Obs length: 110
Timestep: 32


Action: 1
Stacked Frames[0]:  [[  0   0   0 ...   0   0   0]
 [145 145  31 ...  31 145 145]
 [145 145  31 ...  31 145 145]
 ...
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]]
image size[1]: 110
image size[0]: 84
Obs length: 110
Training # 11
Epoch 1/1
 - 0s - loss: 12.3451 - acc: 0.8125
Timestep: 33


Action: 7
Stacked Frames[0]:  [[  0   0   0 ...   0   0   0]
 [145 145  31 ...  31 145 145]
 [145 145  31 ...  31 145 145]
 ...
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]]
image size[1]: 110
image size[0]: 84
Obs length: 110
Timestep: 34
